In [1]:
import datetime
import pandas as pd
from dateutil.relativedelta import relativedelta
import os
import math

In [2]:
def getQuarters(curDate, prevDate):
    
    prevMon = prevDate.strftime("%b")
    curMon = curDate.strftime("%b")
    prevYear = prevDate.strftime("%Y")
    curYear = curDate.strftime("%Y")
    curQuarter = f"{curMon} {curYear}"
    prevQuarter = f"{prevMon} {prevYear}"
    return curQuarter, prevQuarter

def quarterList():
    lst = []
    date = datetime.datetime(2022,12,1)
    minDate = datetime.datetime(2017,1,1)
    while(date > minDate):
        prevDate = date-relativedelta(months=3)
        curQuarter, prevQuarter = getQuarters(date, prevDate)
        lst.append([curQuarter, prevQuarter])
        date = prevDate
    return lst

In [3]:
quarterPairs = quarterList()
quarter_result_dates = pd.read_csv("C:\\Users\\garya\\ML projects\\Stock analysis\\datasets\\quarterlyResultDates.csv", index_col= False)

In [4]:
quarterly_df = pd.read_csv("C:\\Users\\garya\\ML projects\\Stock analysis\\datasets\\quarterlyResultsNSE.csv").set_index('symbol')

In [5]:
quarter_result_dates = quarter_result_dates.fillna("")
quarter_result_dates = quarter_result_dates[quarter_result_dates['nsesymbol'] != '']
quarter_result_dates = quarter_result_dates.reset_index()

In [6]:
print(quarter_result_dates.loc[0])

index                    1
companyname    amjumbobags
companycode           JB03
nsesymbol          AMJUMBO
bsesymbol                 
                  ...     
Mar 1999                  
Sep 1997                  
Mar 1998                  
Mar 1997                  
Dec 1996                  
Name: 0, Length: 110, dtype: object


In [7]:
temp_data = quarter_result_dates.loc[0]

In [8]:
temp_data = temp_data.dropna()
temp_data

index                    1
companyname    amjumbobags
companycode           JB03
nsesymbol          AMJUMBO
bsesymbol                 
                  ...     
Mar 1999                  
Sep 1997                  
Mar 1998                  
Mar 1997                  
Dec 1996                  
Name: 0, Length: 110, dtype: object

In [9]:
#   0         0          0         0
#   8         4          2         1
#(profit) (revenue)  (Ebitda) `(margin)

def getBit(str1, str2):
    print(str1,str2)
#     print(str1, str2)
    if(math.isnan(str1)  or math.isnan(str2)):
        return "hello"
#     a = float(str1)
#     b = float(str2)
#     change = a - b
#     if(change > 0):
#         return 1
    return 0

def generateCategory(prevQuarter, curQuarter, fundamental_row, symbol):
    try:
        ans = 0
        
        marginBit = getBit(fundamental_row[f"Margin {curQuarter}"], fundamental_row[f"Margin {prevQuarter}"])
        ebitdaBit = getBit(fundamental_row[f"EBITDA {curQuarter}"], fundamental_row[f"EBITDA {prevQuarter}"])
        revenueBit = getBit(fundamental_row[f"Revenue {curQuarter}"], fundamental_row[f"Revenue {prevQuarter}"])
        profitBit = getBit(fundamental_row[f"Profit {curQuarter}"], fundamental_row[f"Profit {prevQuarter}"])

        if(dict1.get([marginBit, ebitdaBit,revenueBit, profitBit,symbol], "default") == default):
            dict1[[marginBit, ebitdaBit,revenueBit, profitBit,symbol]].append({symbol, curQuarter})
        if(ans > 15):
            return -1
        return ans
    except Exception as e:
        print("category", e)
        return -1

def getCurPrice(date, symbol, flag=True):
    if(flag):
        date = date.split("-")
        if(len(date) == 1):
            date = date[0].split("/")
        date = datetime.datetime(int(date[2]),int(date[1]),int(date[0]) )
        
    minDate = datetime.datetime(2017,1,1)
    while(date > minDate ):
        try:
            YY = date.strftime("%Y")
            mon = date.strftime("%b").upper()
            dd = date.strftime("%d")
            df = pd.read_csv(f"C:\\Users\\garya\\ML projects\\Stock analysis\\datasets\\nsedataPrevious5years\\cm{dd}{mon}{YY}bhav.csv").set_index("SYMBOL")
            if(symbol not in df.index):
                return -1
            ans = df['CLOSE'][symbol]
            return ans
        except Exception as e:
            x = 1           
#           print(e)
                
        finally:
            date -= datetime.timedelta(days=1)
    return -1

def getHighLowValues(date, symbol):
#     print(symbol)
    high = getCurPrice(date,symbol)
    low = high
    date = date.split("-")
    if(len(date) == 1):
        date = date[0].split("/")
    date = datetime.datetime(int(date[2]),int(date[1]),int(date[0]) )
    for i in range(1,90):
        date += datetime.timedelta(days=1)
        val = float(getCurPrice(date,symbol,False))
        if(val == -1):
            continue
        high = max(high,val )
        low = min(low, val)
    
    return high,low
        

In [10]:
print(getCurPrice("28/02/2021", "3MINDIA"))
print(getHighLowValues("28/02/2021", "3MINDIA"))

22832.75
(30436.65, 22832.75)


In [11]:
quarter_result_dates.iloc[0]

index                    1
companyname    amjumbobags
companycode           JB03
nsesymbol          AMJUMBO
bsesymbol                 
                  ...     
Mar 1999                  
Sep 1997                  
Mar 1998                  
Mar 1997                  
Dec 1996                  
Name: 0, Length: 110, dtype: object

In [71]:
for i in range(len(quarter_result_dates)):
# for i in range(6,7):
    try: 
        date_row = quarter_result_dates.iloc[i]
        print(date_row)
        symbol = date_row['nsesymbol']
        companyname = date_row['companyname']
        companycode = date_row['companycode']
        columns = date_row.index
        fundamental_row = quarterly_df.loc[symbol]
#         print(fundamental_row)
        for qtr in quarterPairs:
            try:
                curQuarter = qtr[0]
                prevQuarter = qtr[1]
                
                if((curQuarter in columns)):
                    generateCategory(prevQuarter, curQuarter, fundamental_row, symbol)

            except Exception as e:
                print("For", e)
            
    except Exception as e:
        print("main", e)

index                    1
companyname    amjumbobags
companycode           JB03
nsesymbol          AMJUMBO
bsesymbol                 
                  ...     
Mar 1999                  
Sep 1997                  
Mar 1998                  
Mar 1997                  
Dec 1996                  
Name: 0, Length: 110, dtype: object
main 'AMJUMBO'
index                     2
companyname    abinfrabuild
companycode             I07
nsesymbol           ABINFRA
bsesymbol                  
                   ...     
Mar 1999                   
Sep 1997                   
Mar 1998                   
Mar 1997                   
Dec 1996                   
Name: 1, Length: 110, dtype: object
main 'ABINFRA'
index                            8
companyname    a2zinfraengineering
companycode                  AME02
nsesymbol                 A2ZINFRA
bsesymbol                 533292.0
                      ...         
Mar 1999                          
Sep 1997                          
Mar 1998     

885.9 722.35
5.39 1.27
8.52 1.93
158.13 151.4
3.71 2.37
Jun 2022 Mar 2022
15
817.0 613.95
1.27 3.88
1.93 5.24
151.4 135.15
2.37 -2.23
Mar 2022 Dec 2021
12
987.3 750.8
3.88 2.93
5.24 4.1
135.15 139.82
-2.23 0.83
Dec 2021 Sep 2021
3
For list index out of range
2.93 5.5
4.1 8.21
139.82 149.15
0.83 4.52
Sep 2021 Jun 2021
0
1311.3 965.25
5.5 6.73
8.21 8.49
149.15 126.17
4.52 5.69
Jun 2021 Mar 2021
4
1785.65 1340.85
6.73 7.9
8.49 8.43
126.17 106.66
5.69 4.78
category must be real number, not str
7.9 8.12
8.43 9.09
106.66 111.89
4.78 6.59
category must be real number, not str
8.12 6.01
9.09 7.28
111.89 121.05
6.59 4.57
Sep 2020 Jun 2020
11
For list index out of range
6.01 6.5
7.28 5.79
121.05 89.13
4.57 3.33
Jun 2020 Mar 2020
14
For list index out of range
6.5 nan
5.79 nan
89.13 nan
3.33 nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan 

96.65 76.4
42.4 30.77
1545.71 1455.38
3645.75 4729.82
197.18 188.29
Jun 2019 Mar 2019
11
104.1 81.0
30.77 36.42
1455.38 1376.89
4729.82 3780.16
188.29 138.72
Mar 2019 Dec 2018
14
104.9 78.5
36.42 34.48
1376.89 1238.07
3780.16 3590.46
138.72 117.18
Dec 2018 Sep 2018
15
116.15 80.5
34.48 38.98
1238.07 1193.85
3590.46 3062.72
117.18 150.05
Sep 2018 Jun 2018
6
For cannot convert the series to <class 'float'>
38.98 27.98
1193.85 1176.06
3062.72 4202.97
150.05 248.82
Jun 2018 Mar 2018
3
160.4 124.25
27.98 10.54
1176.06 350.3
4202.97 3325.02
248.82 262.86
Mar 2018 Dec 2017
7
169.75 145.55
10.54 nan
350.3 nan
3325.02 nan
262.86 nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
index                      34
companyname    abcotspinindia
companycode             ACI01
nsesymbol              ABCOTS
bsesymbol            890161.0
                    ...      
Mar 1999                     
Sep 1997                     
Mar 1998                     
Ma

81.8 70.1
-5.38 -2.21
-1.21 -0.39
22.49 17.61
-1.12 -0.36
Jun 2022 Mar 2022
4
94.0 72.0
-2.21 4.34
-0.39 1.39
17.61 32.01
-0.36 0.93
Mar 2022 Dec 2021
0
112.3 85.3
4.34 7.45
1.39 2.35
32.01 31.55
0.93 2.18
Dec 2021 Sep 2021
4
137.3 97.45
7.45 -3.19
2.35 -1.46
31.55 45.81
2.18 -1.37
Sep 2021 Jun 2021
11
152.4 -1
-3.19 3.65
-1.46 1.11
45.81 30.4
-1.37 1.41
Jun 2021 Mar 2021
4
122.6 -1
3.65 15.56
1.11 9.38
30.4 60.28
1.41 8.07
category must be real number, not str
15.56 7.53
9.38 1.35
60.28 17.92
8.07 1.47
category must be real number, not str
7.53 -4.25
1.35 -0.85
17.92 20.02
1.47 -0.8
Sep 2020 Jun 2020
11
-1 -1
-4.25 -8.35
-0.85 -1.66
20.02 19.89
-0.8 -3.76
Jun 2020 Mar 2020
15
-1 -1
-8.35 -2.83
-1.66 -1.16
19.89 40.92
-3.76 -0.9
Mar 2020 Dec 2019
0
For list index out of range
-2.83 -1.81
-1.16 -0.16
40.92 8.82
-0.9 -0.01
Dec 2019 Sep 2019
4
For list index out of range
-1.81 -0.71
-0.16 -0.2
8.82 28.08
-0.01 -0.16
Sep 2019 Jun 2019
10
For list index out of range
-0.71 -8.49
-0.2 -1.52
2

1759.8 1493.6
8.78 8.7
332.63 292.74
3788.62 3363.96
729.4 206.69
Dec 2018 Sep 2018
15
For list index out of range
8.7 12.63
292.74 475.88
3363.96 3767.9
206.69 326.77
Sep 2018 Jun 2018
0
1543.9 1344.9
12.63 9.66
475.88 343.65
3767.9 3556.99
326.77 247.44
Jun 2018 Mar 2018
15
1662.1 1310.8
9.66 8.32
343.65 284.26
3556.99 3417.14
247.44 202.6
Mar 2018 Dec 2017
15
1587.15 1266.85
8.32 nan
284.26 nan
3417.14 nan
202.6 nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
index                            68
companyname    accelyakalesolutions
companycode                     KAL
nsesymbol                   ACCELYA
bsesymbol                  532268.0
                       ...         
Mar 1999                           
Sep 1997                           
Mar 1998                           
Mar 1997                           
Dec 1996                           
Name: 34, Length: 110, dtype: object
category 'Margin Dec 2022'
36.97 32.05
42.61 33.

...

82.1 67.85
-19.38 -109.64
-1.82 -5.8
9.39 5.29
-1.89 -4.87
Sep 2018 Jun 2018
15
86.25 55.85
-109.64 nan
-5.8 nan
5.29 nan
-4.87 nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
index                     5695
companyname    zenithcomputers
companycode                 ZC
nsesymbol           ZENITHCOMP
bsesymbol             517164.0
                    ...       
Mar 1999            28-04-1999
Sep 1997                      
Mar 1998                      
Mar 1997                      
Dec 1996                      
Name: 2843, Length: 110, dtype: object
main 'ZENITHCOMP'
index                    5698
companyname    zenithinfotech
companycode                ZI
nsesymbol          ZENITHINFO
bsesymbol            532298.0
                    ...      
Mar 1999                     
Sep 1997                     
Mar 1998                     
Mar 1997                     
Dec 1996  

1.55 0.85
-83.72 -551.69
-16.25 -47.28
19.41 8.57
-18.49 -66.57
Dec 2019 Sep 2019
15
2.8 1.55
-551.69 -108.29
-47.28 -10.06
8.57 9.29
-66.57 -17.03
Sep 2019 Jun 2019
0
1.45 0.95
-108.29 -833.25
-10.06 -139.07
9.29 16.69
-17.03 -89.62
Jun 2019 Mar 2019
11
2.9 0.9
-833.25 -122.38
-139.07 -19.3
16.69 15.77
-89.62 -24.98
Mar 2019 Dec 2018
4
7.15 3.35
-122.38 -63.1
-19.3 -11.27
15.77 17.86
-24.98 -26.33
Dec 2018 Sep 2018
8
8.2 4.1
-63.1 -298.83
-11.27 -112.42
17.86 37.62
-26.33 -125.57
Sep 2018 Jun 2018
11
12.45 6.85
-298.83 -580.53
-112.42 -152.33
37.62 26.24
-125.57 -139.17
Jun 2018 Mar 2018
15
14.7 10.35
-580.53 -152.49
-152.33 -75.97
26.24 49.82
-139.17 -101.43
Mar 2018 Dec 2017
0
24.0 15.4
-152.49 -28.78
-75.97 -28.96
49.82 100.62
-101.43 -48.19
Dec 2017 Sep 2017
0
29.95 20.5
-28.78 -7.14
-28.96 -6.37
100.62 89.2
-48.19 -53.43
Sep 2017 Jun 2017
12
24.35 19.75
-7.14 -226.18
-6.37 -175.54
89.2 77.61
-53.43 -197.79
Jun 2017 Mar 2017
15
35.85 20.15
-226.18 4.71
-175.54 9.7
77.61 206.02
-19

423.15 358.5
11.81 12.74
4.18 4.26
35.39 33.44
3.21 3.37
Sep 2021 Jun 2021
4
For list index out of range
12.74 -3.43
4.26 -1.05
33.44 30.59
3.37 -0.73
Jun 2021 Mar 2021
15
426.95 250.75
-3.43 -6.53
-1.05 -1.99
30.59 30.48
-0.73 -1.01
category must be real number, not str
-6.53 0.32
-1.99 0.09
30.48 28.17
-1.01 1.02
category must be real number, not str
0.32 2.34
0.09 0.41
28.17 17.55
1.02 0.51
Sep 2020 Jun 2020
12
161.8 137.15
2.34 2.21
0.41 0.51
17.55 23.08
0.51 0.71
Jun 2020 Mar 2020
1
161.8 140.05
2.21 1.0
0.51 0.25
23.08 25.06
0.71 0.38
Mar 2020 Dec 2019
11
191.35 129.45
1.0 4.35
0.25 1.1
25.06 25.29
0.38 1.09
Dec 2019 Sep 2019
0
191.35 178.95
4.35 2.54
1.1 0.55
25.29 21.68
1.09 0.56
Sep 2019 Jun 2019
15
For list index out of range
2.54 6.65
0.55 1.37
21.68 20.6
0.56 1.15
Jun 2019 Mar 2019
4
For list index out of range
6.65 nan
1.37 nan
20.6 nan
1.15 nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
n

2113.65 1677.6
22.92 23.2
134.83 139.37
588.21 600.75
130.8 133.13
Jun 2021 Mar 2021
0
2418.0 2136.4
23.2 11.5
139.37 43.27
600.75 376.41
133.13 1.77
category must be real number, not str
11.5 6.06
43.27 20.63
376.41 340.32
1.77 -105.34
category must be real number, not str
6.06 21.57
20.63 115.93
340.32 537.37
-105.34 89.2
Sep 2020 Jun 2020
0
For list index out of range
21.57 20.03
115.93 97.7
537.37 487.87
89.2 69.1
Jun 2020 Mar 2020
15
1904.0 1595.9
20.03 8.22
97.7 27.36
487.87 332.67
69.1 4.24
Mar 2020 Dec 2019
15
1486.8 1200.2
8.22 5.09
27.36 16.58
332.67 326.03
4.24 -12.02
Dec 2019 Sep 2019
15
1561.7 1428.5
5.09 18.0
16.58 111.66
326.03 620.25
-12.02 80.4
Sep 2019 Jun 2019
0
For list index out of range
18.0 16.76
111.66 69.74
620.25 416.15
80.4 62.31
Jun 2019 Mar 2019
15
1821.35 1394.6
16.76 24.5
69.74 35.62
416.15 145.41
62.31 40.42
Mar 2019 Dec 2018
14
1340.0 1236.95
24.5 26.36
35.62 36.43
145.41 138.21
40.42 42.16
Dec 2018 Sep 2018
4
1406.05 1109.8
26.36 14.02
36.43 20.05
138.

-1 -1
13.69 13.67
39.33 40.49
287.34 296.15
27.2 14.63
Dec 2019 Sep 2019
9
For list index out of range
13.67 9.32
40.49 26.11
296.15 280.12
14.63 1.37
Sep 2019 Jun 2019
15
-1 -1
9.32 12.7
26.11 38.05
280.12 299.6
1.37 35.2
Jun 2019 Mar 2019
0
-1 -1
12.7 12.02
38.05 36.85
299.6 306.54
35.2 18.02
Mar 2019 Dec 2018
11
For list index out of range
12.02 11.84
36.85 32.39
306.54 273.63
18.02 8.88
Dec 2018 Sep 2018
15
-1 -1
11.84 10.59
32.39 25.62
273.63 241.98
8.88 6.04
Sep 2018 Jun 2018
15
-1 -1
10.59 15.46
25.62 43.17
241.98 279.28
6.04 23.78
Jun 2018 Mar 2018
0
-1 -1
15.46 16.35
43.17 38.84
279.28 237.52
23.78 22.77
Mar 2018 Dec 2017
14
-1 -1
16.35 nan
38.84 nan
237.52 nan
22.77 nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
index                5723
companyname       3mindia
companycode          MI42
nsesymbol         3MINDIA
bsesymbol        523395.0
                  ...    
Mar 1999                 
Sep 1997                 
Mar 199

In [38]:
float()

0.0